In [1]:
import json
import os
import pandas as pd
import pickle
import subprocess
import time
from tqdm import tqdm

In [2]:
def scan_releases(package_releases_path, results_dir):
    package_dirs = [f.path for f in os.scandir(package_releases_path) if f.is_dir()]
    for package_dir in tqdm(package_dirs):
        package_name = f"{package_dir.split('/')[6]}"
        print(package_name)
        subprocess.run(["bandit", "-r", package_dir, "-f", "json", "-o", f"{os.path.join(results_dir, package_name)}.json"])

In [17]:
def calcuate_running_times(package_releases_path, results_dir):
    running_times = {}
    package_dirs = [f.path for f in os.scandir(package_releases_path) if f.is_dir()]
    for package_dir in tqdm(package_dirs):
        package_name = f"{package_dir.split('/')[6]}" 
        start_time = time.time()
        subprocess.run(["bandit", "-r", package_dir,  "-f", "json", "-o", f"{os.path.join(results_dir, package_name)}.json"])
        print(package_name)
        running_times[package_name] = time.time() - start_time
    return running_times

In [4]:
def parse_analysis_results(results_dir):
    results = []
    for root, dirs, files in os.walk(results_dir):
        for file in files:
            file_path = os.path.join(root, file)
            package_name = file_path.split("/")[-1].replace(".json", "")
            with open(file_path, "rb") as f:
                data_bytes = f.read()
                data_str = data_bytes.decode("utf-8", errors='ignore')
                data = json.loads(data_str)
                for result in data["results"]:
                    results.append([package_name, result["filename"], result['issue_text']])
    return results

In [5]:
def get_tp_fp(num_alerts_list, threshold):
    count = 0
    for i in num_alerts_list:
        if i > threshold:
            count = count + 1
    tp = count
    fp = len(num_alerts_list) - tp
    return (tp, fp)

## Malicious packages

In [ ]:
malicious_packages_path = os.path.abspath("../dataset/malicious-packages/")
malicious_results_dir = os.path.abspath("../results/bandit4mal/malicious/")

In [ ]:
scan_releases(malicious_packages_path, malicious_results_dir)

In [ ]:
malicious_results_path = os.path.abspath("../results/bandit4mal/malicious/")
malicious_results = analyze_results(malicious_results_path)

### Triggered rules in all Python files in malicious packages

In [ ]:
malicious_results_df = pd.DataFrame(malicious_results, columns=["package", "target", "rule"])

In [ ]:
# Number of rules per package
malicious_packages_rules_groupby = malicious_results_df.groupby('package')['rule']
print(f"Total number of rules: {malicious_packages_rules_groupby.count().sum()}")
malicious_packages_rules_groupby.count().describe()

### Triggered rules in all setup.py files in malicious packages

In [ ]:
malicious_packages_rules_setup_df = malicious_results_df[malicious_results_df['target'].str.contains('setup.py')]

In [ ]:
# Number of rules per package
malicious_packages_rules_setup_groupby = malicious_packages_rules_setup_df.groupby('package')['rule']
print(f"Total number of rules: {malicious_packages_rules_setup_groupby.count().sum()}")
malicious_packages_rules_setup_groupby.count().describe()

In [ ]:
# Saving the existing result
with open(os.path.abspath("../results/malicious_packages_scanning_results_bandit4mal.pkl"), 'wb') as fp:
    pickle.dump(malicious_results, fp, protocol=pickle.HIGHEST_PROTOCOL)

## Popular packages

In [6]:
# Paths to popular packages and the results dir
popular_packages_path = os.path.abspath("../dataset/popular-packages/")
popular_results_dir = os.path.abspath("../results/bandit4mal/popular/")

In [ ]:
# Scanning popular packages
scan_releases(popular_packages_path, popular_results_dir)

In [18]:
popular_packages_running_time = calcuate_running_times(popular_packages_path, popular_results_dir)

  0%|                                                                                                                                                                                                               | 0/1430 [00:00<?, ?it/s][main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[json]	INFO	JSON output written to file: /home/lyvd/bad-snakes/results/bandit4mal/popular/absl-py.json
  0%|▏                                                                                                                                                                                                      | 1/1430 [00:02<56:52,  2.39s/it]

absl-py


[main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[json]	INFO	JSON output written to file: /home/lyvd/bad-snakes/results/bandit4mal/popular/accelerate.json
  0%|▎                                                                                                                                                                                                    | 2/1430 [00:05<1:00:13,  2.53s/it]

accelerate


[main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[json]	INFO	JSON output written to file: /home/lyvd/bad-snakes/results/bandit4mal/popular/acme.json
  0%|▍                                                                                                                                                                                                    | 3/1430 [00:07<1:00:36,  2.55s/it]

...

factory-boy


[main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[json]	INFO	JSON output written to file: /home/lyvd/bad-snakes/results/bandit4mal/popular/fake-useragent.json
 29%|████████████████████████████████████████████████████████▊                                                                                                                                        | 421/1430 [2:20:16<2:07:52,  7.60s/it]

fake-useragent


[main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
 29%|████████████████████████████████████████████████████████▊                                                                                                                                        | 421/1430 [3:57:05<9:28:14, 33.79s/it]


KeyboardInterrupt: 

In [ ]:
# Parsing the results 
popular_results_path = os.path.abspath("../results/bandit4mal/popular/")
popular_results = parse_analysis_results(popular_results_path)

### Triggered rules in all Python files in popular packages

In [ ]:
# Transform the results into DataFrame for analysis
popular_results_df = pd.DataFrame(popular_results, columns=["package", "target", "rule"])

In [ ]:
# Number of rules per package
popular_packages_rules_groupby = popular_results_df.groupby('package')['rule']
print(f"Total number of rules: {popular_packages_rules_groupby.count().sum()}")
popular_packages_rules_groupby.count().describe()

In [ ]:
# Ratio of true positives to false postives 
thresholds = [1, 5, 10, 15, 20, 25, 30]
scores = popular_packages_rules_groupby.count().to_list()
thesholds_tpr_fpr_ratio = []
for t in thresholds:
    tp, fp = get_tp_fp(scores, t)
    print(t, tp, fp)

### Triggered rules in all setup.py files in popular packages

In [ ]:
popular_packages_rules_setup_df = popular_results_df[popular_results_df['target'].str.contains('setup.py')]

In [ ]:
# Number of rules per package
popular_packages_rules_setup_groupby = popular_packages_rules_setup_df.groupby('package')['rule']
print(f"Total number of rules: {popular_packages_rules_setup_groupby.count().sum()}")
popular_packages_rules_setup_groupby.count().describe()

In [ ]:
# Ratio of true positives to false postives 
thresholds = [1, 2, 3, 4, 5]
scores = popular_packages_rules_groupby.count().to_list()
thesholds_tpr_fpr_ratio = []
for t in thresholds:
    tp, fp = get_tp_fp(scores, t)
    print(t, tp, fp)

In [ ]:
# Saving the existing result
with open(os.path.abspath("../results/bandit4mal/popular-packages.pkl"), 'wb') as fp:
    pickle.dump(popular_results, fp, protocol=pickle.HIGHEST_PROTOCOL)

## Random packages

In [7]:
# Paths to random packags, and results dir
random_packages_path = os.path.abspath("../dataset/random-packages/")
random_results_dir = os.path.abspath("../results/bandit4mal/random/")

In [8]:
random_packages_running_time = calcuate_running_times(random_packages_path, random_results_dir)

  0%|                                                                                                                                           | 0/986 [00:00<?, ?it/s][main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[main]	INFO	running on Python 3.8.10
  0%|▏                                                                                                                                  | 1/986 [00:02<35:59,  2.19s/it]

Run started:2022-08-30 14:18:33.488060

Test results:
>> Issue: [B824:url_found] url_found
   Severity: Medium   Confidence: Medium
   Location: /home/lyvd/bad-snakes/dataset/random-packages/650-auto-comp-jaewon/0.4/650-auto-comp-jaewon-0.4/setup.py:10
   More Info: https://bandit.readthedocs.io/en/latest/plugins/b824_url_found.html
9	  author_email = 'jae1903@gmail.com',      # Type in your E-Mail
10	  url = 'https://github.com/jaewony/650-auto-complete-jaewon.git',   # Provide either the link to your github or to your website
11	  download_url = 'https://github.com/jaewony/650-auto-complete-jaewon/archive/0.4.tar.gz',    # I explain this later on

--------------------------------------------------
>> Issue: [B824:url_found] url_found
   Severity: Medium   Confidence: Medium
   Location: /home/lyvd/bad-snakes/dataset/random-packages/650-auto-comp-jaewon/0.4/650-auto-comp-jaewon-0.4/setup.py:11
   More Info: https://bandit.readthedocs.io/en/latest/plugins/b824_url_found.html
10	  url =

[main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[main]	INFO	running on Python 3.8.10
[tester]	ERROR	Bandit internal error running: exec_used on file /home/lyvd/bad-snakes/dataset/random-packages/a38-decimal/0.1.6/a38-decimal-0.1.6/a38/codec.py at line 252: __init__() got an unexpected keyword argument 'cwe'Traceback (most recent call last):
  File "/usr/local/lib/python3.8/dist-packages/bandit/core/tester.py", line 54, in run_tests
    result = test(context)
  File "/usr/local/lib/python3.8/dist-packages/bandit/plugins/exec.py", line 55, in exec_used
    return exec_issue()
  File "/usr/local/lib/python3.8/dist-packages/bandit/plugins/exec.py", line 43, in exec_issue
    return bandit.Issue(
TypeError: __init__() got an unexpected keyword argument 'cwe'

  0%|▎                                                                                                                             

Run started:2022-08-30 14:18:36.340881

Test results:
>> Issue: [B815:write] os.write
   Severity: High   Confidence: Medium
   Location: /home/lyvd/bad-snakes/dataset/random-packages/a38-decimal/0.1.6/a38-decimal-0.1.6/a38/codec.py:118
   More Info: https://bandit.readthedocs.io/en/latest/plugins/b815_write.html
117	                # Write out the current buffer
118	                tf.write(current)
119	                if error is not None:

--------------------------------------------------
>> Issue: [B832:write] tempfile_NamedTemporaryFile_write
   Severity: High   Confidence: Medium
   Location: /home/lyvd/bad-snakes/dataset/random-packages/a38-decimal/0.1.6/a38-decimal-0.1.6/a38/codec.py:118
   More Info: https://bandit.readthedocs.io/en/latest/plugins/b832_write.html
117	                # Write out the current buffer
118	                tf.write(current)
119	                if error is not None:

--------------------------------------------------
>> Issue: [B815:write] os.write
 

[main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[main]	INFO	running on Python 3.8.10
  0%|▍                                                                                                                                  | 3/986 [00:05<29:14,  1.78s/it]

...

Run started:2022-08-30 14:35:48.371488

Test results:
>> Issue: [B814:read] os.read
   Severity: High   Confidence: Medium
   Location: /home/lyvd/bad-snakes/dataset/random-packages/mergedict/1.0.0/mergedict-1.0.0/setup.py:11
   More Info: https://bandit.readthedocs.io/en/latest/plugins/b814_read.html
10	) as ld_file:
11	    long_description = ld_file.read()
12	

--------------------------------------------------
>> Issue: [B824:url_found] url_found
   Severity: Medium   Confidence: Medium
   Location: /home/lyvd/bad-snakes/dataset/random-packages/mergedict/1.0.0/mergedict-1.0.0/setup.py:21
   More Info: https://bandit.readthedocs.io/en/latest/plugins/b824_url_found.html
20	    long_description = long_description,
21	    url = 'https://github.com/schettino72/mergedict/',
22	    keywords = ['dict', 'singledispatch', 'config'],

--------------------------------------------------

Code scanned:
	Total lines of code: 188
	Total lines skipped (#nosec): 0

Run metrics:
	Total issues (by seve

[main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[main]	INFO	running on Python 3.8.10
 48%|██████████████████████████████████████████████████████████████▍                                                                  | 477/986 [17:18<17:17,  2.04s/it]

Run started:2022-08-30 14:35:49.604325

Test results:
>> Issue: [B823:ip_found] ip_found
   Severity: Medium   Confidence: Medium
   Location: /home/lyvd/bad-snakes/dataset/random-packages/mess-server-leget/0.0.1/mess_server_leget-0.0.1/server/common/settings.py:6
   More Info: https://bandit.readthedocs.io/en/latest/plugins/b823_ip_found.html
5	# IP адрес по умолчанию для подключения клиента
6	DEFAULT_IP_ADDRESS = '127.0.0.1'
7	# Максимальная очередь подключений
8	MAX_CONNECTIONS = 5

--------------------------------------------------
>> Issue: [B814:read] os.read
   Severity: High   Confidence: Medium
   Location: /home/lyvd/bad-snakes/dataset/random-packages/mess-server-leget/0.0.1/mess_server_leget-0.0.1/server/server.py:43
   More Info: https://bandit.readthedocs.io/en/latest/plugins/b814_read.html
42	    dir_path = os.getcwd()
43	    config.read(f"{dir_path}/{'server.ini'}")
44	    # Если конфиг файл

[main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[main]	INFO	running on Python 3.8.10
 48%|██████████████████████████████████████████████████████████████▌                                                                  | 478/986 [17:18<13:48,  1.63s/it][main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[main]	INFO	running on Python 3.8.10
 49%|██████████████████████████████████████████████████████████████▋                                                                  | 479/986 [17:19<10:55,  1.29s/it][main]	INFO	profile include tests: None
[main]	INFO	profile exclude tests: None
[main]	INFO	cli include tests: None
[main]	INFO	cli exclude tests: None
[main]	INFO	running on Python 3.8.10
 49%|██████████████████████████████████████████████████████████████▊                             

KeyboardInterrupt: 

In [ ]:
# Scanning random packages
scan_releases(random_packages_path, random_results_dir)

In [ ]:
# Analyzing the results generated
random_results_path = os.path.abspath("../results/bandit4mal/random/")
random_results = parse_analysis_results(random_results_path)

### Triggered rules in all Python files in random packages

In [ ]:
# Transform the results into Dataframe for analysis
random_results_df = pd.DataFrame(random_results, columns=["package", "target", "rule"])

In [ ]:
# Number of rules per package
random_packages_rules_groupby = random_results_df.groupby('package')['rule']
print(f"Total number of rules: {random_packages_rules_groupby.count().sum()}")
random_packages_rules_groupby.count().describe()

In [ ]:
# Ratio of true positives to false postives 
thresholds = [1, 5, 10, 15, 20, 25, 30]
scores = random_packages_rules_groupby.count().to_list()
thesholds_tpr_fpr_ratio = []
for t in thresholds:
    tpr, fpr = get_tpr_fpr(scores, t)
    print(t, round(tpr/fpr, 2))

### Triggered rules in all setup.py files in random packages

In [ ]:
# Selecting only setup.py files of the packages
random_packages_rules_setup_df = random_results_df[random_results_df['target'].str.contains('setup.py')]

In [ ]:
# Number of rules per package
random_packages_rules_setup_groupby = random_packages_rules_setup_df.groupby('package')['rule']
print(f"Total number of rules: {random_packages_rules_setup_groupby.count().sum()}")
random_packages_rules_setup_groupby.count().describe()

In [ ]:
# Ratio of true positives to false postives 
thresholds = [1, 2, 3, 4, 5]
scores = random_packages_rules_setup_groupby.count().to_list()
thesholds_tpr_fpr_ratio = []
for t in thresholds:
    tp, fp = get_tp_fp(scores, t)
    print(t, tp, fp)

In [ ]:
# Saving the existing result
with open(os.path.abspath("../results/bandit4mal/random-packages.pkl"), 'wb') as fp:
    pickle.dump(random_results, fp, protocol=pickle.HIGHEST_PROTOCOL)